In [1]:
# Copyright 2025 Keysight Technologies Inc.

In [2]:
import numpy as np
import keysight.qcs as qcs
from keysight.qcs.experiments import make_calibration_set
from keysight.qcs.experiments import CrossResonance

In [3]:
# Set this to True if channel mapper exists
channel_mapper_exists = False

if channel_mapper_exists:
    mapper = qcs.load("<path/to/channel_mapper.qcs>")
else:
    # generate an empty channel mapper with the correct address
    mapper = qcs.ChannelMapper("127.0.0.1")

In [4]:
n_qubits = 2
qubits = qcs.Qudits(range(n_qubits))
edge_list = [(0, 1)]
mq_targets = qubits.make_connectivity(edge_list)
calibration_set = make_calibration_set(n_qubits, edge_list)

# Set this to True if connected to hardware
run_on_hw = False

In [5]:
# Create a resonator spectroscopy experiment
cross_resonance = CrossResonance(
    backend=mapper,
    calibration_set=calibration_set,
    qubits=mq_targets,
    operation="CR",
)

In [6]:
# Draw the program to view the hardware operations
cross_resonance.draw()

In [7]:
# Retrieve the amplitude stored in the calibration set
current_freq = cross_resonance.calibration_set.variables.cr_gate_amplitude.value

# Set the frequency range for sweeping
start = 0
end = 0.5
nsteps = 10
freq_scan_values = np.linspace(start, end, nsteps)

In [8]:
# Configure the repetitions for this experiment
cross_resonance.configure_repetitions(
    n_shots=1, cr_amplitudes=freq_scan_values, hw_sweep=False
)

In [9]:
if run_on_hw:
    cross_resonance.execute()
else:
    # load in a previously executed version of this experiment
    cross_resonance = qcs.load("CrossResonance.qcs")

In [10]:
# Plot the trace waveforms
cross_resonance.plot_trace()